<a href="https://colab.research.google.com/github/oalopez/poc-geodata/blob/main/PoC_FitIdeas%2BExperian_CO.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Requerimiento PoC - Frontera Agricola

Fragmento del correo con requerimiento:

*De acuerdo con lo conversado, te comparto la idea que tengo de PoC hacia nuestros clientes que utiliza la información que nos suministraste. Solicito por favor de tu apoyo con la creación de un notebook que compile la siguiente idea:*

*Con la información que nos suministraste de UPRA_Nacional se requiere pintar polígonos espaciales de las áreas que son prohibidas para la explotación agropecuaria (ver referencia Creating Spatial Polygons en: https://pygis.io/docs/c_new_vectors.html)
Nuestro cliente puede suministrar información georreferenciada de 2 formas:
Proporciona una longitud y latitud
Proporciona una serie de longitudes y latiitudes que conforman un polígono
El objetivo de la PoC es validar si los datos enviados por un cliente están o no dentro del poligono espacial (1) y sacar un mensaje de “Precaución: La ubicación suministrada está en un área restringida” o “Adelante: La ubicación suministrada no está en área restringida.*

**CELDA 1:** Instalar librerías

In [1]:
!pip install pandas
!pip install geopandas
!pip install shapely
!pip install folium

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 9.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 47.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.1/16.1 MB 44.9 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


**CELDA 2:** importar librerías requeridas

In [2]:
import pandas as pd
import geopandas as gpd
import shapely.wkt
import folium
import pyproj
import shapely.geometry
import shapely.ops

**CELDA 3:** pintar multipoligonos de archivo **poc_frontera_agricola.v2.0.csv**



In [4]:
# Read the data from the CSV file, the separator is a pipe (|) and encoding is UTF-8
data = pd.read_csv('poc_frontera_agricola.v2.0.csv', sep='|', encoding='utf-8')

# Convert the WKT-formatted geometry column to a GeoDataFrame
data['geometry'] = data['geometry'].apply(shapely.wkt.loads)
gdf = gpd.GeoDataFrame(data, geometry='geometry')

# Set the CRS of the GeoDataFrame
#1683576,894435 EPSG:3116
gdf.crs = "EPSG:3116"

# Transform the CRS of the GeoDataFrame to EPSG:4326
gdf = gdf.to_crs("EPSG:4326")

# Define the colors for each zone
colors = {
    'Bosques naturales y áreas no agropecuarias': 'orange',
    'Frontera agrícola nacional': 'darkgreen',
    'Exclusiones legales': 'darkred',
}

# Define the HTML code for the legend
legend_html = '''
<div style="position: fixed; bottom: 50px; left: 50px; width: 350px;  
             border:2px solid grey; z-index:9999; font-size:14px; background: rgba(255, 255, 255, 0.7);">
    <span style='background: darkgreen; width: 20px; height: 20px; display: inline-block;'></span>
    Bosques naturales y áreas no agropecuarias<br>
    <span style='background: darkblue; width: 20px; height: 20px; display: inline-block;'></span>
    Frontera agrícola nacional<br>
    <span style='background: darkred; width: 20px; height: 20px; display: inline-block;'></span>
    Exclusiones legales
</div>
'''


# Create a map centered in the first lat long found in the data
m = folium.Map(location=[10.784, -74.943], zoom_start=12, tiles='Stamen Toner')

# Add the HTML legend to the map
m.get_root().html.add_child(folium.Element(legend_html))

# Define a function to style each feature based on its zone type
def style_function(feature):
    zone_type = feature['properties']['elemento']
    color = colors.get(zone_type, 'gray')
    return {'fillColor': color, 'color': 'transparent'}

zone_geometries = {}

# Add a layer for each zone type with its corresponding color
for zone_type, color in colors.items():
    zone_gdf = gdf[gdf['elemento'] == zone_type]
    zone_geometry = zone_gdf.unary_union
    zone_geometries[zone_type] = zone_geometry

    # create the GeoJson layer
    geojson_layer = folium.GeoJson(zone_gdf, style_function=style_function)

    # create the tooltip object
    tooltip = folium.GeoJsonTooltip(fields=["elemento"])

    # add the tooltip to the GeoJson layer
    geojson_layer.add_child(tooltip)

    # add the GeoJson layer to the map
    geojson_layer.add_to(m)
    #add the GeoJSON data to the map with the color defined above
    #folium.GeoJson(zone_gdf, style_function=style_function).add_to(m)

# Show the map
m


**CELDA 4**: Solictud de punto o polígono al usuario

In [10]:

import pyproj
import shapely.geometry

def check_points_in_zones(points, zone_geometries):
    """
    Check if points are inside any of the zone geometries.
    
    Args:
    - points: list of tuple of float, point coordinates in (latitude, longitude) format.
    - zone_geometries: dictionary, containing zone types as keys and shapely.geometry objects as values.
    
    Returns:
    - A list containing tuples for each point:
        - A boolean indicating whether the point is inside any of the zone geometries.
        - A string indicating the zone type that the point is inside. Empty string if not inside any zone.
    """
    point_zones = []
    
    for point in points:
        # Convert coordinates to the same projection as the GeoDataFrame
        point_proj = pyproj.transform(pyproj.Proj('EPSG:4326'), pyproj.Proj(gdf.crs), point[1], point[0])
        point_geom = shapely.geometry.Point(point_proj)

        # Check if point is inside any zone
        inside_zone = False
        zone_type = ''
        for z_type, zone_geometry in zone_geometries.items():
            # Create a small buffer around the point (radius 100 meters)
            buffer = point_geom.buffer(0.001)

            # Check if the buffer intersects with the polygon
            if buffer.intersects(zone_geometry):
                inside_zone = True
                zone_type = z_type
                break
        
        point_zones.append((inside_zone, zone_type))
    
    return point_zones


# Ask for the number of points to add
num_points = int(input("Enter the number of points to add: "))

# Ask the user for four coordinate tuples and create a polygon
coords = []
for i in range(num_points):
    lat_lon = input("Enter a tuple of coordinates (lat, lon): ")
    lat, lon = map(float, lat_lon.split(','))
    coords.append((lat, lon))

# Add the first coordinate to the end of the list to close the polygon
if len(coords) > 1:
    coords.append(coords[0])

# Check if points are inside any zone
point_zones = check_points_in_zones(coords, zone_geometries)

# Print zone types of each point in the polygon
for i, (inside, zone) in enumerate(point_zones):
    print(f"Point {i + 1}: {zone}")

if len(coords) > 1: # Polygon

    #if all points are inside the same zone, color the polygon with that zone's color and add a tooltip
    #if all points are not inside any zone, color the polygon gray and add a tooltip
    #if points are inside different zones, color the polygon gray and add a tooltip
    in_or_out = ''
    if all([point_zones[0][0] == point_zones[i][0] for i in range(len(point_zones))]):
        if point_zones[0][0]:
            if point_zones[0][1] == 'Exclusiones legales':
                color = 'coral'
            elif point_zones[0][1] == 'Frontera agrícola nacional':
                color = 'green'
            elif point_zones[0][1] == 'Bosques naturales y áreas no agropecuarias':
                color = 'orange'
            in_or_out = 'Todos los puntos están dentro de la zona ' + point_zones[0][1]
        else:
            color = 'gray'
            in_or_out = 'Todos los puntos están fuera de las zonas delimitadas'

    elif any([point_zones[0][0] != point_zones[i][0] for i in range(len(point_zones))]):
        color = 'gray'
        in_or_out = 'Algunos puntos están dentro de las zonas delimitadas y otros no'

    # Add the polygon to the map
    folium.Polygon(locations=coords,
        color='gray',
        fill_color=color,
        fill_opacity=0.7,
        tooltip=in_or_out,
        weight=0.1
        ).add_to(m)


else: # Point
    # Add a marker to the map at the specified coordinates
    if point_zones[0][0]:
        if point_zones[0][1] == 'Exclusiones legales':
            color = 'coral'
        elif point_zones[0][1] == 'Frontera agrícola nacional':
            color = 'green'
        elif point_zones[0][1] == 'Bosques naturales y áreas no agropecuarias':
            color = 'orange'
        tooltip = point_zones[0][1]
    else:
        color = 'gray'
        tooltip = 'Zona no delimitada'

    folium.Marker(location=coords[0], 
        icon=folium.Icon(color=color), 
        tooltip=tooltip).add_to(m)

    
# Show the map
m


Enter the number of points to add: 4
Enter a tuple of coordinates (lat, lon): 10.787496,-74.921249
Enter a tuple of coordinates (lat, lon): 10.787429,-74.919294
Enter a tuple of coordinates (lat, lon): 10.786270,-74.919059
Enter a tuple of coordinates (lat, lon): 10.785837,-74.920231


<ipython-input-10-497f1cfbd8c9>:21: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  point_proj = pyproj.transform(pyproj.Proj('EPSG:4326'), pyproj.Proj(gdf.crs), point[1], point[0])
<ipython-input-10-497f1cfbd8c9>:21: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  point_proj = pyproj.transform(pyproj.Proj('EPSG:4326'), pyproj.Proj(gdf.crs), point[1], point[0])
<ipython-input-10-497f1cfbd8c9>:21: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  point_proj = pyproj.transform(pyproj.Proj('EPSG:4326'), pyproj.Proj(gdf.crs), point[1], point[0])
<ipython-input-10-497f1cfbd8c9>:21: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  po

Point 1: Bosques naturales y áreas no agropecuarias
Point 2: Bosques naturales y áreas no agropecuarias
Point 3: Bosques naturales y áreas no agropecuarias
Point 4: Bosques naturales y áreas no agropecuarias
Point 5: Bosques naturales y áreas no agropecuarias
